# Deep Learning for Time Series Forecasting

Data: https://www.kaggle.com/competitions/competitive-data-science-predict-future-sales/data

Reference code: https://www.kaggle.com/code/dimitreoliveira/deep-learning-for-time-series-forecasting/data?select=train.csv

Credits to DIMITREOLIVEIRA


- LSTM

In [88]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [89]:
%cd /content/drive/MyDrive/딥러닝기초

/content/drive/MyDrive/딥러닝기초


## Dependencies

In [90]:
!pip install chart-studio

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [91]:
import warnings
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from keras import optimizers
from keras.utils import plot_model
from keras.models import Sequential, Model
from keras.layers.convolutional import Conv1D, MaxPooling1D
from keras.layers import Dense, LSTM, RepeatVector, TimeDistributed, Flatten
from sklearn.metrics import mean_squared_error
from sklearn.model_selection import train_test_split
from chart_studio import plotly
import plotly.graph_objs as go
from plotly.offline import init_notebook_mode, iplot

%matplotlib inline
warnings.filterwarnings("ignore")
init_notebook_mode(connected=True)

# Set seeds to make the experiment more reproducible.
import tensorflow
import pandas as pd
from numpy.random import seed
tensorflow.random.set_seed(1)

## Data Upload

In [92]:
# We need to define the 'date' feature as date type by passing it into 'parse_dates' parameter.
# Without this, pandas will read 'date' feature as string(object)
train_df = pd.read_csv('./demand-forecasting-kernels-only/train.csv',parse_dates=['date'])
display(train_df.head(2))
train_df.info()

date  store  item  sales
0 2013-01-01      1     1     13
1 2013-01-02      1     1     11

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 913000 entries, 0 to 912999
Data columns (total 4 columns):
 #   Column  Non-Null Count   Dtype         
---  ------  --------------   -----         
 0   date    913000 non-null  datetime64[ns]
 1   store   913000 non-null  int64         
 2   item    913000 non-null  int64         
 3   sales   913000 non-null  int64         
dtypes: datetime64[ns](1), int64(3)
memory usage: 27.9 MB


In [93]:
test_df = pd.read_csv('./demand-forecasting-kernels-only/test.csv',parse_dates=['date'])
display(test_df.head(2))
test_df.info()

id       date  store  item
0   0 2018-01-01      1     1
1   1 2018-01-02      1     1

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 45000 entries, 0 to 44999
Data columns (total 4 columns):
 #   Column  Non-Null Count  Dtype         
---  ------  --------------  -----         
 0   id      45000 non-null  int64         
 1   date    45000 non-null  datetime64[ns]
 2   store   45000 non-null  int64         
 3   item    45000 non-null  int64         
dtypes: datetime64[ns](1), int64(3)
memory usage: 1.4 MB


No missing values in our datasets.

Since we are aiming for Time Series Forecasting, time feature plays important role. 

In [94]:
print(train_df['date'].min())
print(train_df['date'].max())

2013-01-01 00:00:00
2017-12-31 00:00:00


Calculate the number of days to be forecast 

In [95]:
max_date_train = train_df['date'].max().date()
max_date_test = test_df['date'].max().date()
print(f'Forecast lag size : {(max_date_test-max_date_train).days} days')

lag_size = (max_date_test-max_date_train).days

Forecast lag size : 90 days


## Basic EDA

In [96]:
train_df['date'].value_counts().sort_index()

2013-01-01    500
2013-01-02    500
2013-01-03    500
2013-01-04    500
2013-01-05    500
             ... 
2017-12-27    500
2017-12-28    500
2017-12-29    500
2017-12-30    500
2017-12-31    500
Name: date, Length: 1826, dtype: int64

To explore the time series data first we need to aggregate the sales by day

In [97]:
# Use as_index = False in groupby to leave date as column and not as index
daily_sales = train_df.groupby('date', as_index=False)['sales'].sum()

In [98]:
store_daily_sales = train_df.groupby(['store','date'], as_index=False)['sales'].sum()

In [99]:
item_daily_sales = train_df.groupby(['item','date'], as_index=False)['sales'].sum()

### Plot daily sales

In [100]:
daily_sales_sc = go.Scatter(x=daily_sales['date'], y=daily_sales['sales'])
layout = go.Layout(title='Daily sales', xaxis=dict(title='Date'), yaxis=dict(title='Sales'))
fig = go.Figure(data=[daily_sales_sc], layout=layout)
fig.show(renderer="colab")

### Plot daily sales by store

In [101]:
store_daily_sales_sc = []
for store in store_daily_sales['store'].unique(): # loop over each store
    # subdataframe 
    current_store_daily_sales = store_daily_sales[(store_daily_sales['store'] == store)]
    # append scatterplot in the list 
    store_daily_sales_sc.append(go.Scatter(x=current_store_daily_sales['date'], y=current_store_daily_sales['sales'], name=('Store %s' % store)))

layout = go.Layout(title='Store daily sales', xaxis=dict(title='Date'), yaxis=dict(title='Sales'))
fig = go.Figure(data=store_daily_sales_sc, layout=layout)
fig.show(renderer="colab")

### Plot daily sales by item

In [102]:
item_daily_sales_sc = []
for item in item_daily_sales['item'].unique(): # loop over each store
    # subdataframe 
    current_item_daily_sales = item_daily_sales[(item_daily_sales['item'] == store)]
    # append scatterplot in the list 
    item_daily_sales_sc.append(go.Scatter(x=current_item_daily_sales['date'], y=current_item_daily_sales['sales'], name=('Store %s' % store)))

#plot
layout = go.Layout(title='Item daily sales', xaxis=dict(title='Date'), yaxis=dict(title='Sales'))
fig = go.Figure(data=item_daily_sales_sc, layout=layout)
iplot(fig)

## Data Preparation

Sub-sample train set to get only the last year of data and reduce training time.

In [103]:
train_df2017 = train_df[(train_df['date'] >= '2017-01-01')]

In [104]:
train_gp = train_df2017.sort_values('date').groupby(['item', 'store', 'date'], as_index=False)
train_gp = train_gp.agg({'sales':['mean']})
train_gp.columns = ['item', 'store', 'date', 'sales']
train_gp.head()

item  store       date  sales
0     1      1 2017-01-01   19.0
1     1      1 2017-01-02   15.0
2     1      1 2017-01-03   10.0
3     1      1 2017-01-04   16.0
4     1      1 2017-01-05   14.0

## Data Transformation 
(into time series problem)

In [105]:
def series_to_supervised(data, window=1, lag=1, dropnan=True):
    cols, names = list(), list()
    # Input sequence (t-n, ... t-1)
    for i in range(window, 0, -1):
        cols.append(data.shift(i))
        names += [('%s(t-%d)' % (col, i)) for col in data.columns]
    # Current timestep (t=0)
    cols.append(data)
    names += [('%s(t)' % (col)) for col in data.columns]
    # Target timestep (t=lag)
    cols.append(data.shift(-lag))
    names += [('%s(t+%d)' % (col, lag)) for col in data.columns]
    # Put it all together
    agg = pd.concat(cols, axis=1)
    agg.columns = names
    # Drop rows with NaN values
    if dropnan:
        agg.dropna(inplace=True)
    return agg

We will use the current timestep and the last 29 to forecast 90 days ahead

In [106]:
window = 29
lag = lag_size
series = series_to_supervised(train_gp.drop('date', axis=1), window=window, lag=lag)
series.head()

item(t-29)  store(t-29)  sales(t-29)  item(t-28)  store(t-28)  \
29         1.0          1.0         19.0         1.0          1.0   
30         1.0          1.0         15.0         1.0          1.0   
31         1.0          1.0         10.0         1.0          1.0   
32         1.0          1.0         16.0         1.0          1.0   
33         1.0          1.0         14.0         1.0          1.0   

    sales(t-28)  item(t-27)  store(t-27)  sales(t-27)  item(t-26)  ...  \
29         15.0         1.0          1.0         10.0         1.0  ...   
30         10.0         1.0          1.0         16.0         1.0  ...   
31         16.0         1.0          1.0         14.0         1.0  ...   
32         14.0         1.0          1.0         24.0         1.0  ...   
33         24.0         1.0          1.0         14.0         1.0  ...   

    sales(t-2)  item(t-1)  store(t-1)  sales(t-1)  item(t)  store(t)  \
29        16.0        1.0         1.0        24.0        1         1   
30        24.0        1.0         1.0         9.0        1         1   
31         9.0        1.0         1.0        17.0        1         1   
32        17.0        1.0         1.0        15.0        1         1   
33        15.0        1.0         1.0        17.0        1         1   

    sales(t)  item(t+90)  store(t+90)  sales(t+90)  
29       9.0         1.0          1.0         33.0  
30      17.0         1.0          1.0         15.0  
31      15.0         1.0          1.0         21.0  
32      17.0         1.0          1.0         29.0  
33      24.0         1.0          1.0         19.0  

[5 rows x 93 columns]

Drop rows with different item or store values than the shifted columns

In [107]:
last_item = 'item(t-%d)' % window
last_store = 'store(t-%d)' % window
series = series[(series['store(t)'] == series[last_store])]
series = series[(series['item(t)'] == series[last_item])]

Remove unwanted columns

In [108]:
columns_to_drop = [('%s(t+%d)' % (col, lag)) for col in ['item', 'store']]
for i in range(window, 0, -1):
    columns_to_drop += [('%s(t-%d)' % (col, i)) for col in ['item', 'store']]
series.drop(columns_to_drop, axis=1, inplace=True)
series.drop(['item(t)', 'store(t)'], axis=1, inplace=True)

## Train - & Validation split

In [109]:
# Label
labels_col = 'sales(t+%d)' % lag_size
labels = series[labels_col]
series = series.drop(labels_col, axis=1)

X_train, X_valid, Y_train, Y_valid = train_test_split(series, labels.values, test_size=0.4, random_state=0)
print('Train set shape', X_train.shape)
print('Validation set shape', X_valid.shape)
X_train.head()

Train set shape (100746, 30)
Validation set shape (67164, 30)


sales(t-29)  sales(t-28)  sales(t-27)  sales(t-26)  sales(t-25)  \
18801          97.0        111.0         90.0        115.0        123.0   
160385         38.0         43.0         43.0         55.0         47.0   
73123          55.0         45.0         41.0         46.0         47.0   
90428         139.0        157.0         85.0         99.0        136.0   
167151         86.0         58.0         88.0         87.0        114.0   

        sales(t-24)  sales(t-23)  sales(t-22)  sales(t-21)  sales(t-20)  ...  \
18801          70.0         99.0         74.0        107.0        108.0  ...   
160385         51.0         38.0         41.0         37.0         59.0  ...   
73123          36.0         30.0         46.0         41.0         42.0  ...   
90428         110.0        121.0        123.0        147.0         91.0  ...   
167151        113.0         64.0         76.0         87.0         81.0  ...   

        sales(t-9)  sales(t-8)  sales(t-7)  sales(t-6)  sales(t-5)  \
18801         85.0        95.0       123.0       109.0       127.0   
160385        41.0        38.0        38.0        53.0        53.0   
73123         38.0        36.0        40.0        50.0        44.0   
90428        130.0       128.0       128.0        95.0       116.0   
167151        55.0        66.0        59.0        53.0        63.0   

        sales(t-4)  sales(t-3)  sales(t-2)  sales(t-1)  sales(t)  
18801        132.0        87.0       101.0       102.0     114.0  
160385        45.0        44.0        24.0        30.0      37.0  
73123         44.0        40.0        38.0        50.0      49.0  
90428        110.0       117.0       118.0       129.0     132.0  
167151        59.0        77.0        39.0        56.0      62.0  

[5 rows x 30 columns]

## LSTM for Time Series Forecasting

the LSTM model actually sees the input data as a sequence, so it's able to learn patterns from sequenced data (assuming it exists) better than the other ones, especially patterns from long sequences.
Input shape [samples, timesteps, features].

Reshape from [samples, timesteps] into [samples, timesteps, features]

The input of the LSTM layer is [batch, timesteps, feature] 

In [110]:
X_train_series = X_train.values.reshape((X_train.shape[0], X_train.shape[1], 1))
X_valid_series = X_valid.values.reshape((X_valid.shape[0], X_valid.shape[1], 1))
print('Train set shape', X_train_series.shape)
print('Validation set shape', X_valid_series.shape)

Train set shape (100746, 30, 1)
Validation set shape (67164, 30, 1)


In [111]:
epochs = 40
batch = 256
lr = 0.0003
adam = optimizers.Adam(lr)

In [112]:
model_lstm = Sequential()
model_lstm.add(LSTM(50, activation='relu', input_shape=(X_train_series.shape[1], X_train_series.shape[2])))
model_lstm.add(Dense(1))
model_lstm.compile(loss='mse', optimizer=adam)
model_lstm.summary()

Model: "sequential_3"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 lstm_2 (LSTM)               (None, 50)                10400     
                                                                 
 dense_2 (Dense)             (None, 1)                 51        
                                                                 
Total params: 10,451
Trainable params: 10,451
Non-trainable params: 0
_________________________________________________________________


In [113]:
lstm_history = model_lstm.fit(X_train_series, Y_train, validation_data=(X_valid_series, Y_valid), epochs=epochs, verbose=2)

Epoch 1/40
3149/3149 - 58s - loss: 503.8380 - val_loss: 370.9846 - 58s/epoch - 18ms/step
Epoch 2/40
3149/3149 - 53s - loss: 372.2098 - val_loss: 367.1808 - 53s/epoch - 17ms/step
Epoch 3/40
3149/3149 - 54s - loss: 364.5769 - val_loss: 374.1483 - 54s/epoch - 17ms/step
Epoch 4/40
3149/3149 - 52s - loss: 358.1614 - val_loss: 361.0178 - 52s/epoch - 16ms/step
Epoch 5/40
3149/3149 - 52s - loss: 355.5738 - val_loss: 347.9118 - 52s/epoch - 17ms/step
Epoch 6/40
3149/3149 - 52s - loss: 352.6449 - val_loss: 356.0083 - 52s/epoch - 16ms/step
Epoch 7/40
3149/3149 - 52s - loss: 350.5911 - val_loss: 375.4498 - 52s/epoch - 16ms/step
Epoch 8/40
3149/3149 - 53s - loss: 349.3753 - val_loss: 345.3845 - 53s/epoch - 17ms/step
Epoch 9/40
3149/3149 - 51s - loss: 348.2553 - val_loss: 353.3952 - 51s/epoch - 16ms/step
Epoch 10/40
3149/3149 - 52s - loss: 347.8459 - val_loss: 350.8685 - 52s/epoch - 17ms/step
Epoch 11/40
3149/3149 - 53s - loss: 346.0912 - val_loss: 346.9916 - 53s/epoch - 17ms/step
Epoch 12/40
3149/31

In [114]:
lstm_train_pred = model_lstm.predict(X_train_series)
lstm_valid_pred = model_lstm.predict(X_valid_series)
print('Train rmse:', np.sqrt(mean_squared_error(Y_train, lstm_train_pred)))
print('Validation rmse:', np.sqrt(mean_squared_error(Y_valid, lstm_valid_pred)))

2099/2099 [==============================] - 12s 6ms/step
Train rmse: 18.14642488409607
Validation rmse: 18.292843190801058
